<a href="https://colab.research.google.com/github/CJunji/AdaptiveFiltering/blob/main/LMS_Variantion_EC_and_NC.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# TB312 - Aplicações envolvendo técnicas de processamento de sinais
### Módulo 2 - Fundamentos de filtragem adaptativa

---
**Discente 1: Caio Junji**

**Discente 2: Pedro**

**Prof. Eduardo Vinícius Kuhn**  

**Instituição:** Universidade Tecnológica Federal do Paraná (UTFPR)  
**Departamento:** Engenharia Eletrônica

---

<table>
<tr>
<td valign="top"> <!-- Tabela de Comandos Markdown -->

### Comandos úteis para células Markdown
| Comando             | Ação                             |
|---------------------|----------------------------------|
| `#`                 | Título de nível 1 (maior)        |
| `##`                | Título de nível 2                |
| `###`               | Título de nível 3                |
| `-` ou `*`          | Item de lista não ordenada       |
| `1.`, `2.`, etc.    | Item de lista ordenada           |
| `**texto**`         | Texto em negrito                 |
| `*texto*` ou `_texto_` | Texto em itálico             |

</td>
<td width="20"> <!-- Espaço vazio entre as colunas -->
</td>
<td valign="top"> <!-- Tabela de Atalhos do Google Colab -->

### Atalhos úteis no Google Colab
| Atalho              | Ação                                          |
|---------------------|-----------------------------------------------|
| `Ctrl + Enter`      | Executar célula                               |
| `Shift + Enter`     | Executar célula e ir para a próxima           |
| `Alt + Enter`       | Executar célula e inserir uma nova abaixo     |
| `Ctrl + /`          | Comentar a linha atual                        |
| `Ctrl + M + Y`      | Converte célula para código                   |
| `Ctrl + M + M`      | Converte célula para markdown                 |
| `Ctrl + M + A`      | Inserir célula de código acima                |
| `Ctrl + M + B`      | Inserir célula de código abaixo               |
| `Ctrl + M + D`      | Deletar célula                                |
| `Ctrl + M + Z`      | Desfazer última ação (dentro de uma célula)   |
| `Ctrl + M + H`      | Localizar e substituir                        |

</td>
</tr>
</table>


# Importar bibliotecas

In [1]:
import os, requests
import numpy as np
from scipy.io import loadmat
from IPython.display import Audio, display

# Algoritmos utilizados

## NLMS

In [2]:
def NLMS_algorithm(N, M, mu, w0, x, d):

    #prevenir divisao por 0
    epsilon = 1

    # Pré-aloca memória com zeros
    x_temp = np.zeros(M)
    y, e, w = np.zeros(N), np.zeros(N), w0

    # Executa o algoritmo NLMS
    for k in range(N):

        # Desloca as amostras e insere um novo valor na primeira posição
        x_temp[1:], x_temp[0] = x_temp[:-1], x[k]

        # Filtra a entrada
        y[k] = np.dot(w, x_temp)

        # Calcula o erro
        e[k] = d[k] - y[k]

        # Atualiza o vetor de coeficientes
        w = w + (mu * e[k] * x_temp / (epsilon + np.dot(x_temp.T, x_temp)))

    return e

## Sign LMS

In [3]:
def sign(x):
    return np.where(x >= 0, 1, -1)

def sign_LMS(N, M, mu, w0, x, d):
    # Pré-aloca memória com zeros
    x_temp = np.zeros(M)
    y, e, w = np.zeros(N), np.zeros(N), w0

    # Executa o algoritmo Sign Regressor LMS
    for k in range(N):
        # Desloca as amostras e insere um novo valor na primeira posição
        x_temp[1:], x_temp[0] = x_temp[:-1], x[k]

        # Filtra a entrada
        y[k] = np.dot(w, x_temp)

        # Calcula o erro
        e[k] = d[k] - y[k]

        # Atualiza o vetor de coeficientes
        w = w + (mu * sign(e[k]) * x_temp)

    return e

## Sign Regressor

In [4]:
def sign_regressor_LMS(N, M, mu, w0, x, d):
    # Pré-aloca memória com zeros
    x_temp = np.zeros(M)
    y, e, w = np.zeros(N), np.zeros(N), w0

    # Executa o algoritmo Sign Regressor LMS
    for k in range(N):
        # Desloca as amostras e insere um novo valor na primeira posição
        x_temp[1:], x_temp[0] = x_temp[:-1], x[k]

        # Filtra a entrada
        y[k] = np.dot(w, x_temp)

        # Calcula o erro
        e[k] = d[k] - y[k]

        # Atualiza o vetor de coeficientes
        w = w + (mu * e[k] * sign(x_temp))

    return e

## Leaky LMS

In [5]:
def leaky_LMS(N, M, mu, w0, x, d):

    # gamma
    gamma = 0.95

    # Pré-aloca memória com zeros
    x_temp = np.zeros(M)
    x_T_temp = np.zeros(M)
    y, e, w = np.zeros(N), np.zeros(N), w0

    # Executa o algoritmo NLMS
    for k in range(N):

        # Desloca as amostras e insere um novo valor na primeira posição
        x_temp[1:], x_temp[0] = x_temp[:-1], x[k]

        # Filtra a entrada
        y[k] = np.dot(w, x_temp)

        # Calcula o erro
        e[k] = d[k] - y[k]

        # Atualiza o vetor de coeficientes
        w = ((1 - (mu * gamma)) * w) + (mu * e[k] * x_temp)

    return e

## Avaliação de resultado


### Cancelamento de eco

In [6]:
def estimativa_erle(eco, res_eco, L=4096):

    # Calcular a média das potências das últimas L amostras dos sinais
    pot_eco, pot_res_eco = np.mean(eco[-L:]**2), np.mean(res_eco[-L:]**2)

    # Retorna a ERLE em dB
    return  10 * np.log10(pot_eco / pot_res_eco)

###Cancelamento de ruído

In [7]:
def estimativa_nrr(sinal_corrompido, sinal_processado, L=4096):
    # Calcular a potência do sinal e do ruído
    pot_ruido_antes, pot_ruido_depois = np.mean(sinal_corrompido[-L:]**2), np.mean(sinal_processado[-L:]**2)

    # Calcular a NRR em dB
    return 10 * np.log10(pot_ruido_antes / pot_ruido_depois)

# Experimento 2

Para o desenvolvimento do presente experimento, [acesse o repositório](https://github.com/eduardovkuhn/aplicacoes_proc_sinais/tree/8a724d4dc162ae8ced67cb12678db5575b16fae9/experimentos/experimento%202) e proceda a leitura dos documentos indicados. A partir disso, você estará apto a desenvolver a presente atividade com sucesso.

## Cancelamento de eco

Um cancelador adaptativo de eco visa minimizar o efeito do eco presente em um sistema de comunicação. Para tal, os coeficientes do filtro adaptativo $\mathbf{w}(n)$ são ajustados dinamicamente, através de um algoritmo adaptativo, a fim de produzir uma estimativa $\hat{d}(n)$ do eco $d(n)$ que retorna pela linha. Então, realizando a subtração no domínio elétrico, i.e.,
$$ e(n) = d(n) - \hat{d}(n)$$
torna-se possível eliminar/remover o eco e melhorar a qualidade da ligação telefônica.

![Topologia de cancelamento de eco.](https://raw.githubusercontent.com/eduardovkuhn/aplicacoes_proc_sinais/main/figuras/topologia_EC.png)


**Etapas**
- Identificar os sinais envolvidos na aplicação
- Modificar o código de forma a atenuar o eco presente no sinal
- Verificar o resultado através do fone de ouvido


**Referencias:**
- Simon Haykin, *Adaptive Filter Theory*, 5th ed., Pearson: Harlow, U.K., 2013.



## Importando dados

In [8]:
# URL do arquivo .mat
url = 'https://raw.githubusercontent.com/eduardovkuhn/aplicacoes_proc_sinais/main/extra/EC_data.mat'
local_filename = 'EC_data.mat'

# Função para baixar o arquivo do URL
def download_file(url, local_filename):
    with requests.get(url, stream=True) as r:
        r.raise_for_status()
        with open(local_filename, 'wb') as f:
            for chunk in r.iter_content(chunk_size=8192):
                f.write(chunk)

# Verifica se o arquivo já existe localmente
if not os.path.exists(local_filename):
    download_file(url, local_filename)
    print('Download concluído.')

# Carrega arquivo de áudio
data = loadmat(local_filename)

# Extraindo os sinais
fs, sinal, sinal_eco = data['Fs'].flatten()[0], data['sinal'].flatten(), data['sinal_eco'].flatten()

Download concluído.


## Áudios importados

In [9]:
# Função para exibir e reproduzir áudio no Colab
def play_audio(signal, sample_rate):
    display(Audio(data=signal, rate=sample_rate))

# Para reproduzir os sinais
print('Sinal transmitido pela linha')
play_audio(sinal, fs)

print('Eco que retorna pela linha')
play_audio(sinal_eco, fs)

print('Efeito do eco para o usuário')
play_audio(sinal + sinal_eco, fs)

Sinal transmitido pela linha


Eco que retorna pela linha


Efeito do eco para o usuário


# Implementação de cancelamento de eco
Serão utilizados os algoritmos definidos anteriormente para cancelamento de eco

## NLMS

In [10]:
M = 1024
w0 = np.zeros(M)
N = len(sinal)

# Filtragem de eco
erroNLMSEC = NLMS_algorithm(N, M, 0.1, w0, sinal, sinal_eco)

print('Efeito do eco para o usuário')
play_audio(sinal + erroNLMSEC, fs)


erle_dB = estimativa_erle(sinal_eco, erroNLMSEC)
print(f'ERLE (dB): {erle_dB:.2f} dB')

Efeito do eco para o usuário


ERLE (dB): 11.67 dB


## Sign LMS

In [11]:
erroSLMSEC = sign_LMS(N, M, 0.0001, w0, sinal, sinal_eco)

erle_dB = estimativa_erle(sinal_eco, erroSLMSEC)
print(f'ERLE (dB): {erle_dB:.2f} dB')

ERLE (dB): 11.59 dB


## Sign Regressor LMS

In [12]:
erroSRLMSEC = sign_regressor_LMS(N, M, 0.001, w0, sinal, sinal_eco)

erle_dB = estimativa_erle(sinal_eco, erroSRLMSEC)
print(f'ERLE (dB): {erle_dB:.2f} dB')

ERLE (dB): 11.66 dB


## Leaky LMS

In [13]:
erroLLMSEC = leaky_LMS(N,M, 0.005, w0, sinal, sinal_eco)

erle_dB = estimativa_erle(sinal_eco, erroLLMSEC)
print(f'ERLE (dB): {erle_dB:.2f} dB')

ERLE (dB): 0.41 dB


## Cancelamento adaptativo de ruído

Um cancelador adaptativo de ruído visa minimizar o efeito do ruído presente em um dado sinal (entrada primária), usando para isso um sinal correlacionado com o ruído que corrompe o sinal de interesse (entrada de referência). Para tal, os coeficientes do filtro adaptativo $\mathbf{w}(n)$ são ajustados dinamicamente, através de um algoritmo adaptativo, a fim de produzir uma estimativa $\hat{d}(n)$ do ruído $d(n)$ que corrompe o sinal de interesse $s(n)$, i.e.,
$$r(n) = s(n) + d(n).$$
Então, realizando a subtração no domínio elétrico, i.e.,
$$e(n) = r(n) - \hat{d}(n)$$
torna-se possível eliminar/remover o ruído e melhorar a qualidade do sinal de áudio.

<!-- ### **Topologia** -->
![Topologia de cancelamento adaptativo de ruído.](https://raw.githubusercontent.com/eduardovkuhn/aplicacoes_proc_sinais/main/figuras/topologia_ANC.png)



**Etapas**
- Identificar os sinais envolvidos na aplicação
- Modificar o código de forma a atenuar o eco presente no sinal
- Verificar o resultado através do fone de ouvido


**Referencias:**
- Simon Haykin, *Adaptive Filter Theory*, 5th ed., Pearson: Harlow, U.K., 2013.

## Importar áudios

In [14]:
# URL do arquivo .mat
url = 'https://raw.githubusercontent.com/eduardovkuhn/aplicacoes_proc_sinais/main/extra/ANC_data.mat'
local_filename = 'ANC_data.mat'

# Função para baixar o arquivo do URL
def download_file(url, local_filename):
    with requests.get(url, stream=True) as r:
        r.raise_for_status()
        with open(local_filename, 'wb') as f:
            for chunk in r.iter_content(chunk_size=8192):
                f.write(chunk)

# Verifica se o arquivo já existe localmente
if not os.path.exists(local_filename):
    download_file(url, local_filename)
    print('Download concluído.')

# Carrega arquivo de áudio
data = loadmat(local_filename)

# Extraindo os sinais
fs, ruido, sinal_ruido = data['Fs'].flatten()[0], data['ruido'].flatten(), data['sinal_ruido'].flatten()

Download concluído.


## Áudios importados

In [15]:
# Função para exibir e reproduzir áudio no Colab
def play_audio(signal, sample_rate):
    display(Audio(data=signal, rate=sample_rate))

# Para reproduzir os sinais
print('Sinal corrompido por ruído')
play_audio(sinal_ruido, fs)

print('Ruído capturado pelo sensor secundário')
play_audio(ruido, fs)

Sinal corrompido por ruído


Ruído capturado pelo sensor secundário


# Cancelamento de ruído
## NLMS

In [16]:
M = 80
w0 = np.zeros(M)

# Para reproduzir os sinais
print('Sinal corrompido por ruído')
play_audio(sinal_ruido, fs)

print('Ruído capturado pelo sensor secundário')
play_audio(ruido, fs)

# Filtragem do sinal
erroNLMSNC = NLMS_algorithm(N, M, 0.08, w0, ruido, sinal_ruido)

nrr_valor = estimativa_nrr(sinal_ruido, erroNLMSNC)
print(f'NRR (dB): {nrr_valor:.2f} dB')

print('Sinal processado')
play_audio(erroNLMSNC, fs)

Sinal corrompido por ruído


Ruído capturado pelo sensor secundário


NRR (dB): 12.44 dB
Sinal processado


## Sign LMS

In [17]:
erroSLMSNC = sign_LMS(N, M, 0.003, w0, ruido, sinal_ruido)

nrr_valor = estimativa_nrr(sinal_ruido, erroSLMSNC)
print(f'NRR (dB): {nrr_valor:.2f} dB')

print('Sinal processado')
play_audio(erroSLMSNC, fs)

NRR (dB): 12.58 dB
Sinal processado


## Sign Regressor LMS

In [18]:
erroSRLMSNC = sign_regressor_LMS(N, M, 0.0002, w0, ruido, sinal_ruido)

nrr_valor = estimativa_nrr(sinal_ruido, erroSRLMSNC)
print(f'NRR (dB): {nrr_valor:.2f} dB')

print('Sinal processado')
play_audio(erroSRLMSNC, fs)

NRR (dB): 12.64 dB
Sinal processado


## Leaky LMS

In [19]:
erroLLMSNC = leaky_LMS(N, M, 0.05, w0, ruido, sinal_ruido)

nrr_valor = estimativa_nrr(sinal_ruido, erroLLMSNC)
print(f'NRR (dB): {nrr_valor:.2f} dB')

print('Sinal processado')
play_audio(erroLLMSNC, fs)

NRR (dB): 0.09 dB
Sinal processado
